In [3]:
import json
import ast

all_q_a = []
X = []
y = []

with open("qa_baby.json") as f:

    for line in f:
        json_line = ast.literal_eval(line)
        json_data = json.dumps(json_line)
        json_data = json.loads(json_data)
        all_q_a.append(json_data)


print("number of question/answers %i" % len(all_q_a))

#for qa in all_q_a:
for count in range(0, 5000):
    qa = all_q_a[count]
    X.append(qa["question"].lower())
    y.append(qa["answer"].lower())


print("count in X %i" % len(X))
print("count in Y %i" % len(y))

number of question/answers 28933
count in X 5000
count in Y 5000


In [4]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.3)
x_test, x_val, y_test, y_val = train_test_split(x_test, y_test, test_size=0.5)

print("count x_train %i" % len(x_train))
print("count y_train %i" % len(y_train))
print("count x_test %i" % len(x_test))
print("count y_test %i" % len(y_test))
print("count x_val %i" % len(x_val))
print("count y_val %i" % len(y_val))

count x_train 3500
count y_train 3500
count x_test 750
count y_test 750
count x_val 750
count y_val 750


In [5]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(min_df=1)
X_vec = vectorizer.fit_transform(X)
print(len(X_vec.indices))

63606


In [6]:
print(x_test[0])
question = vectorizer.transform([x_test[0]])
print(question.indices)

will this fit the davinci sleigh toddler bed the length seems to be off about 4 inches so im curoius if anyone bought this for that toddler bed.
[4652 4269 4267 4221 4190 4187 3801 3754 3575 2813 2372 2132 2113 2107 1760
 1701 1235 1200  663  545  538  377  228]


In [16]:
def benchmark(clf, x_set, y_set, x_test_set, y_test_set):
    print('_' * 80)
    print("Training: ")
    print(clf)
    t0 = time()
    clf.fit(x_set, y_set)
    train_time = time() - t0
    print("train time: %0.3fs" % train_time)

    t0 = time()
    pred = clf.predict(x_test_set)
    test_time = time() - t0
    print("test time:  %0.3fs" % test_time)

    score = metrics.accuracy_score(y_test_set, pred)
    print("accuracy:   %0.3f" % score)

    if hasattr(clf, 'coef_'):
        print("dimensionality: %d" % clf.coef_.shape[1])
        print("density: %f" % density(clf.coef_))

        if opts.print_top10 and feature_names is not None:
            print("top 10 keywords per class:")
            for i, label in enumerate(target_names):
                top10 = np.argsort(clf.coef_[i])[-10:]
                print(trim("%s: %s" % (label, " ".join(feature_names[top10]))))
        print()


    print("classification report:")
    print(metrics.classification_report(y_test_set, pred))

    
    print("confusion matrix:")
    print(metrics.confusion_matrix(y_test_set, pred))

    print()
    clf_descr = str(clf).split('(')[0]
    return clf_descr, score, train_time, test_time




    

In [17]:
from keras.preprocessing import sequence

x_q_vectors = []
for question in x_train:
    indices = vectorizer.transform([question]).indices
    x_q_vectors.append(indices)
    
x_q_vectors = sequence.pad_sequences(x_q_vectors, maxlen=500)
print(len(x_q_vectors))


3500


In [18]:
x_test_q_vectors = []
for question in x_test:
    indices = vectorizer.transform([question]).indices
    x_test_q_vectors.append(indices)
    
x_test_q_vectors = sequence.pad_sequences(x_test_q_vectors, maxlen=500)
#print(x_test_q_vectors)

In [19]:
from time import time
import matplotlib.pyplot as plt
from sklearn.linear_model import RidgeClassifier
from sklearn.pipeline import Pipeline
from sklearn.svm import LinearSVC
from sklearn.linear_model import SGDClassifier
from sklearn.linear_model import Perceptron
from sklearn.linear_model import PassiveAggressiveClassifier
from sklearn.naive_bayes import BernoulliNB, MultinomialNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neighbors import NearestCentroid
from sklearn.ensemble import RandomForestClassifier
from sklearn.utils.extmath import density
from sklearn import metrics


results = []
#for clf, name in (
        #(RidgeClassifier(tol=1e-2, solver="lsqr"), "Ridge Classifier"),
        #(Perceptron(n_iter=50), "Perceptron"),
        #(PassiveAggressiveClassifier(n_iter=50), "Passive-Aggressive"),
        #(KNeighborsClassifier(n_neighbors=10), "kNN"),
        #(RandomForestClassifier(n_estimators=100), "Random forest")):
name = "Random forest"
clf = RandomForestClassifier(n_estimators=100,  n_jobs=10)
        
print('=' * 80)
print(name)

#clf.fit(x_q_vectors, y_train)

results.append(benchmark(clf, x_q_vectors, y_train, x_test_q_vectors, y_test))




Random forest
________________________________________________________________________________
Training: 
RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_split=1e-07, min_samples_leaf=1,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            n_estimators=100, n_jobs=10, oob_score=False,
            random_state=None, verbose=0, warm_start=False)
train time: 3.039s
test time:  0.671s
accuracy:   0.204
classification report:
                                                                                                                                                                                                                                                                                                                                                                                                                                              

/usr/local/lib/python3.4/dist-packages/sklearn/metrics/classification.py:1113: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/usr/local/lib/python3.4/dist-packages/sklearn/metrics/classification.py:1115: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)


In [33]:
question_index = 2
print("question: " + x_val[question_index])
question_vectors = []

indices = vectorizer.transform([x_val[question_index]]).indices
question_vectors.append(indices)

question_vectors = sequence.pad_sequences(question_vectors, maxlen=500)

question: does it come with the screws that it needs to be mounted at top of staircase?


In [34]:

res = clf.predict(question_vectors[0])
print(res)

['no']


/usr/local/lib/python3.4/dist-packages/sklearn/utils/validation.py:395: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  DeprecationWarning)
